In [3]:
!pip install cassandra-driver

     |████████████████████████████████| 3.8 MB 10.4 MB/s eta 0:00:01
  Using cached geomet-0.2.1.post1-py3-none-any.whl (18 kB)


In [1]:
import pandas as pd
import numpy as np
import time
import matplotlib.pyplot as plt
import psutil
import random
from cassandra.cluster import Cluster

In [2]:
#Ficheros de salida
resultados_etl_CutomerProfileSchema = '../Results/Cassandra/CassandraCustomerProfileSchema_{}_rows_{}.csv'
resultados_etl_PositionKeepingSchema = '../Results/Cassandra/CassandraresultsPositionKeepingSchema_{}_rows_{}.csv'
resultados_etl_CurrentAccountSchema = '../Results/Cassandra/CassandraCurrentAccountSchema_{}_rows_{}.csv'
resultados_borrado_CutomerProfileSchema = '../Results/Cassandra/CassandraCustomerProfileSchema_{}_rows_{}.csv'
resultados_borrado_PositionKeepingSchema = '../Results/Cassandra/CassandraresultsPositionKeepingSchema_{}_rows_{}.csv'
resultados_borrado_CurrentAccountSchema = '../Results/Cassandra/CassandraCurrentAccountSchema_{}_rows_{}.csv'

In [3]:
def save_results_to_csv(results,file):
    #Guardamos los resultados en csv
    from datetime import datetime
    dia = datetime.now().strftime("%d%m%Y_%H_%M_%S")    
    print(file.format(len(results) ,str(dia)))
    results.to_csv(file.format(len(results),str(dia)))

In [4]:
cluster = Cluster(['0.0.0.0','localhost'],port=9042)
session = cluster.connect('CustomerProfileKeySpace',wait_for_all_pools=True)
rows = session.execute("DESCRIBE keyspaces")
for row in rows:
    print(row)

Row(keyspace_name='currentaccountkeyspace', type='keyspace', name='currentaccountkeyspace')
Row(keyspace_name='"CustomerProfileKeySpace"', type='keyspace', name='"CustomerProfileKeySpace"')
Row(keyspace_name='customerprofilekeyspace', type='keyspace', name='customerprofilekeyspace')
Row(keyspace_name='positionkeepingkeyspace', type='keyspace', name='positionkeepingkeyspace')
Row(keyspace_name='system', type='keyspace', name='system')
Row(keyspace_name='system_auth', type='keyspace', name='system_auth')
Row(keyspace_name='system_distributed', type='keyspace', name='system_distributed')
Row(keyspace_name='system_schema', type='keyspace', name='system_schema')
Row(keyspace_name='system_traces', type='keyspace', name='system_traces')
Row(keyspace_name='system_views', type='keyspace', name='system_views')
Row(keyspace_name='system_virtual_schema', type='keyspace', name='system_virtual_schema')


# Carga masiva CurrentAccountKeySpace dominio CurrentAccount para modelo columnar

In [5]:
CurrentAccount_csv_file = "../MockData/CurrentAccount.csv"
AccountInfo_csv_file = "../MockData/AccountInfo.csv"

In [6]:
CurrentAccount_df = pd.read_csv(CurrentAccount_csv_file, header=[0])
del(CurrentAccount_df['Unnamed: 8'])
CurrentAccount_df['Status'] = CurrentAccount_df['Status'].str.replace("'",'')
CurrentAccount_df['AccountType'] = CurrentAccount_df['AccountType'].str.replace("'",'')
CurrentAccount_df['AccountSubType'] = CurrentAccount_df['AccountSubType'].str.replace("'",'')
CurrentAccount_df.sample(5)

AccountId  PartyId    Status    StatusUpdateDateTime AccountType  \
7942       7943     7943   Enabled  1988-09-10 16:48:08.00    Business   
5503       5504     5504   Enabled  2014-08-27 23:18:36.00  Particular   
2163       2164     2164  Disabled  2004-09-11 04:57:07.00    Business   
9310       9311     9311  Disabled  2011-08-19 07:16:45.00  Particular   
3798       3799     3799   Enabled  1978-06-17 21:00:22.00  Particular   

                             NickName             OpeningDate AccountSubType  
7942     monetize strategic paradigms  2009-12-15 18:06:32.00            POI  
5503  streamline best-of-breed models  1977-06-21 19:04:58.00            SAI  
2163   facilitate world-class systems  1978-06-01 01:41:02.00            EDP  
9310       harness 24/365 experiences  2012-12-07 23:21:29.00            SAI  
3798  benchmark value-added mindshare  2000-01-23 11:17:12.00            SAI

In [7]:
AccountInfo_df = pd.read_csv(AccountInfo_csv_file, header=[0])
del(AccountInfo_df['Unnamed: 5'])
AccountInfo_df['SchemeName'] = AccountInfo_df['SchemeName'].str.replace("'",'')
SchemeNameList=['ES.OBIE.SortCodeAccountNumber','UK.OBIE.ExternalccountNumber','ES.OBIE.ExternalAccountNumber']
AccountInfo_df['SchemeName'] = np.resize(SchemeNameList,len(AccountInfo_df))

IdentificationList=['Investment','Money Market','Mortgage','Loan']
AccountInfo_df['Identification'] = np.resize(IdentificationList,len(AccountInfo_df))

AccountInfo_df.sample(5)

AccountInfoId  AccountId                     SchemeName Identification  \
9823           9824       9824   UK.OBIE.ExternalccountNumber           Loan   
6455           6456       6456  ES.OBIE.ExternalAccountNumber           Loan   
4424           4425       4425  ES.OBIE.ExternalAccountNumber     Investment   
8821           8822       8822   UK.OBIE.ExternalccountNumber   Money Market   
1861           1862       1862   UK.OBIE.ExternalccountNumber   Money Market   

                           Name  
9823               Schulist LLC  
6455  Corwin, Becker and Wisozk  
4424                  Hyatt Ltd  
8821                Wolff Group  
1861  Keebler, Murazik and Cole

In [24]:
#Generamos un dataset con el formato desnormalizado de nuestro modelo columnar para CurrentAccount

In [8]:
for x in range(12):
    CurrentAccount_df = CurrentAccount_df.append(CurrentAccount_df.sample(frac=0.50,replace = True))
CurrentAccount_df = CurrentAccount_df.iloc[:1000000,]    
print(len(CurrentAccount_df))
CurrentAccount_df.tail()

1000000


AccountId  PartyId    Status    StatusUpdateDateTime AccountType  \
7059       7060     7060   Enabled  1975-03-17 11:10:53.00  Particular   
1911       1912     1912  Disabled  2003-12-04 21:54:58.00    Business   
2823       2824     2824   Enabled  1991-01-05 17:04:22.00  Particular   
6834       6835     6835  Disabled  2001-08-06 17:10:54.00  Particular   
9198       9199     9199  Disabled  1989-02-27 03:41:02.00  Particular   

                                NickName             OpeningDate  \
7059          exploit holistic platforms  1983-05-31 22:45:11.00   
1911                 utilize B2C systems  1984-12-30 05:13:20.00   
2823  maximize user-centric technologies  1997-05-09 20:23:34.00   
6834          morph 24/7 functionalities  2002-08-02 20:29:21.00   
9198           scale viral relationships  1971-10-15 05:44:50.00   

     AccountSubType  
7059            EDP  
1911            POI  
2823            SAI  
6834            SAI  
9198            EDP

In [9]:
for x in range(12):
    AccountInfo_df = AccountInfo_df.append(AccountInfo_df.sample(frac=0.50,replace = True))  
del(AccountInfo_df['AccountInfoId'])
del(AccountInfo_df['AccountId'])
list_accountid = []
AccountInfo_df = AccountInfo_df.iloc[:1000000,]    
print(len(AccountInfo_df))  
AccountInfo_df.tail()

1000000


SchemeName Identification  \
4494  ES.OBIE.SortCodeAccountNumber       Mortgage   
2261  ES.OBIE.ExternalAccountNumber   Money Market   
7776  ES.OBIE.SortCodeAccountNumber     Investment   
2828  ES.OBIE.ExternalAccountNumber     Investment   
774   ES.OBIE.SortCodeAccountNumber       Mortgage   

                             Name  
4494           Wilkinson-Kassulke  
2261             Stanton-Turcotte  
7776  Roberts, McGlynn and Legros  
2828                 Lemke-Feeney  
774    Jacobs, Lakin and Lubowitz

In [10]:
# sE crean ficheros por cada rango
range_row_register = [1000, 10000, 100000, 250000, 500000, 750000, 1000000]

In [11]:
chunks = len(CurrentAccount_df) // 1000
previous_chunk = 0
CurrentAccount_df_chunks_array = []
for i in range(0,chunks):
    chunks = chunks + 1297
    CurrentAccount_df_chunks_array.append(CurrentAccount_df.iloc[previous_chunk:chunks,])     
    previous_chunk = chunks
len(CurrentAccount_df_chunks_array) 

1000

In [12]:
chunks = len(AccountInfo_df) // 1000
previous_chunk = 0
AccountInfo_df_chunks_array = []
for i in range(0,chunks):
    chunks = chunks + 1297
    AccountInfo_df_chunks_array.append(AccountInfo_df.iloc[previous_chunk:chunks,])     
    previous_chunk = chunks
len(AccountInfo_df_chunks_array) 

1000

In [13]:
session.execute("""DROP TABLE CurrentAccountKeySpace.CurrentAccount;""")
session.execute("""CREATE TABLE CurrentAccountKeySpace.CurrentAccount (   PartyId text,   AccountId bigint,   StatusUpdateDateTime timestamp,   AccountType text,   NickName text,   AccountInfo frozen<list<AccountInfo>>,   OpeningDate timestamp,   Status text,   PRIMARY KEY ((AccountId, PartyId), Status) ) WITH CLUSTERING ORDER BY (Status ASC);""")

In [ ]:
#engine.execute('ALTER TABLE CurrentAccountDomainSchema.CurrentAccount ALTER AccountId SET DEFAULT 0')
registers_CurrentAccount_df = []
iter = 0

insert = """insert into CurrentAccountKeySpace.CurrentAccount(AccountId,PartyId,Status,StatusUpdateDateTime,AccountType,NickName,OpeningDate) values(?,?,?,?,?,?,?);"""
prepared_currentaccount = session.prepare(insert)

for item in CurrentAccount_df.iterrows():
#for item in range(0,1):
    iter = iter + 1
    tiempo_ini = time.time()
   
    print(item)

    #Insert
    try:               
        session.execute(prepared_currentaccount, (item[0],item[1],item[2],item[3],item[4],item[5],item[6]))
    except Exception as e:  
        print ("An error occured : " + str(e))
        pass

    tiempo_fin = time.time()
    used_cpu = psutil.cpu_percent()
    used_mem = psutil.virtual_memory().percent
    registers_CurrentAccount_df.append((iter * 1000, round((tiempo_fin - tiempo_ini),3), used_cpu, used_mem))

(0, AccountId                                     1
PartyId                                       1
Status                                 Disabled
StatusUpdateDateTime     2015-03-09 16:45:49.00
AccountType                            Business
NickName                generate 24/7 bandwidth
OpeningDate              2014-03-08 20:17:20.00
AccountSubType                              POI
Name: 0, dtype: object)
An error occured : tuple index out of range
(1, AccountId                                                   2
PartyId                                                     2
Status                                                Enabled
StatusUpdateDateTime                   2012-12-16 17:32:43.00
AccountType                                        Particular
NickName                revolutionize open-source initiatives
OpeningDate                            2002-05-05 03:35:24.00
AccountSubType                                            SAI
Name: 1, dtype: object)
An error occured : t

(314, AccountId                                       315
PartyId                                         315
Status                                      Enabled
StatusUpdateDateTime         1994-11-22 02:48:57.00
AccountType                              Particular
NickName                extend holistic initiatives
OpeningDate                  2007-09-16 10:22:44.00
AccountSubType                                  SAI
Name: 314, dtype: object)
An error occured : tuple index out of range
(315, AccountId                                           316
PartyId                                             316
Status                                          Enabled
StatusUpdateDateTime             2001-11-17 18:18:27.00
AccountType                                  Particular
NickName                visualize visionary convergence
OpeningDate                      2019-04-16 10:19:41.00
AccountSubType                                      POI
Name: 315, dtype: object)
An error occured : tuple ind

(623, AccountId                                         624
PartyId                                           624
Status                                       Disabled
StatusUpdateDateTime           2001-12-30 03:50:47.00
AccountType                                  Business
NickName                unleash one-to-one e-business
OpeningDate                    1982-09-11 12:30:17.00
AccountSubType                                    EDP
Name: 623, dtype: object)
An error occured : tuple index out of range
(624, AccountId                                                    625
PartyId                                                      625
Status                                                  Disabled
StatusUpdateDateTime                      1982-11-17 12:18:31.00
AccountType                                             Business
NickName                transform cross-platform functionalities
OpeningDate                               2013-10-28 21:01:19.00
AccountSubType                 

(926, AccountId                                        927
PartyId                                          927
Status                                      Disabled
StatusUpdateDateTime          2017-04-24 10:53:53.00
AccountType                               Particular
NickName                syndicate robust webservices
OpeningDate                   1999-03-19 15:13:57.00
AccountSubType                                   POI
Name: 926, dtype: object)
An error occured : tuple index out of range
(927, AccountId                                        928
PartyId                                          928
Status                                      Disabled
StatusUpdateDateTime          1991-09-06 15:47:44.00
AccountType                                 Business
NickName                productize global e-business
OpeningDate                   1978-06-20 18:32:25.00
AccountSubType                                   POI
Name: 927, dtype: object)
An error occured : tuple index out of range


(1235, AccountId                                             1236
PartyId                                               1236
Status                                            Disabled
StatusUpdateDateTime                2006-10-15 01:26:44.00
AccountType                                       Business
NickName                visualize user-centric convergence
OpeningDate                         1997-03-17 03:31:04.00
AccountSubType                                         POI
Name: 1235, dtype: object)
An error occured : tuple index out of range
(1236, AccountId                                    1237
PartyId                                      1237
Status                                   Disabled
StatusUpdateDateTime       1989-12-29 14:45:33.00
AccountType                            Particular
NickName                syndicate dynamic markets
OpeningDate                1989-10-19 05:06:41.00
AccountSubType                                SAI
Name: 1236, dtype: object)
An error occured

...

(3929, AccountId                                        3930
PartyId                                          3930
Status                                        Enabled
StatusUpdateDateTime           1979-01-02 16:07:11.00
AccountType                                Particular
NickName                implement strategic solutions
OpeningDate                    1973-06-09 20:27:37.00
AccountSubType                                    EDP
Name: 3929, dtype: object)
An error occured : tuple index out of range
(966, AccountId                                     967
PartyId                                       967
Status                                   Disabled
StatusUpdateDateTime       1992-04-14 05:51:52.00
AccountType                              Business
NickName                drive value-added vortals
OpeningDate                1987-03-23 03:29:07.00
AccountSubType                                SAI
Name: 966, dtype: object)
An error occured : tuple index out of range
(2587, Account

(8203, AccountId                                          8204
PartyId                                            8204
Status                                          Enabled
StatusUpdateDateTime             2016-05-26 09:02:21.00
AccountType                                  Particular
NickName                facilitate leading-edge systems
OpeningDate                      2007-10-29 02:28:32.00
AccountSubType                                      SAI
Name: 8203, dtype: object)
An error occured : tuple index out of range
(2930, AccountId                                   2931
PartyId                                     2931
Status                                  Disabled
StatusUpdateDateTime      1982-11-14 01:15:52.00
AccountType                             Business
NickName                scale sticky convergence
OpeningDate               1999-01-09 10:05:23.00
AccountSubType                               EDP
Name: 2930, dtype: object)
An error occured : tuple index out of range
(165

(5664, AccountId                                      5665
PartyId                                        5665
Status                                      Enabled
StatusUpdateDateTime         2014-08-09 13:13:31.00
AccountType                              Particular
NickName                enhance world-class vortals
OpeningDate                  1989-11-30 01:33:19.00
AccountSubType                                  POI
Name: 5664, dtype: object)
An error occured : tuple index out of range
(4302, AccountId                                         4303
PartyId                                           4303
Status                                        Disabled
StatusUpdateDateTime            1979-06-15 18:54:29.00
AccountType                                 Particular
NickName                transition value-added portals
OpeningDate                     2019-05-04 01:23:28.00
AccountSubType                                     POI
Name: 4302, dtype: object)
An error occured : tuple index o

(9883, AccountId                                                  9884
PartyId                                                    9884
Status                                                  Enabled
StatusUpdateDateTime                     1986-01-18 03:43:44.00
AccountType                                          Particular
NickName                recontextualize mission-critical models
OpeningDate                              2013-02-21 05:27:55.00
AccountSubType                                              EDP
Name: 9883, dtype: object)
An error occured : tuple index out of range
(9166, AccountId                                         9167
PartyId                                           9167
Status                                        Disabled
StatusUpdateDateTime            2018-02-25 15:30:01.00
AccountType                                 Particular
NickName                enable cross-platform eyeballs
OpeningDate                     1989-08-07 03:33:30.00
AccountSubType    

(6042, AccountId                                          6043
PartyId                                            6043
Status                                          Enabled
StatusUpdateDateTime             2010-09-23 10:15:19.00
AccountType                                  Particular
NickName                visualize extensible e-commerce
OpeningDate                      1975-12-22 21:54:24.00
AccountSubType                                      SAI
Name: 6042, dtype: object)
An error occured : tuple index out of range
(7124, AccountId                                      7125
PartyId                                        7125
Status                                     Disabled
StatusUpdateDateTime         1991-07-07 10:52:45.00
AccountType                                Business
NickName                empower interactive portals
OpeningDate                  2008-09-28 09:16:31.00
AccountSubType                                  EDP
Name: 7124, dtype: object)
An error occured : tuple